In [1]:
import sys
sys.path.append('..')
from transport_frames.graphbuilder.graph import Graph 
import geopandas as gpd
from shapely import Polygon, MultiPolygon
import momepy
import pandas as pd
import osmnx as ox

/Users/polina/Desktop/tf2/venv/lib/python3.10/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


## Graph

In [2]:
# creating full leningrad oblast polygon from Saint-P + leningrad oblast
lo_polygon = ox.geocode_to_gdf('R176095', by_osmid=True).to_crs(epsg=32636)
spb_polygon = ox.geocode_to_gdf('R337422', by_osmid=True).to_crs(epsg=32636).buffer(3000)
city = lo_polygon.union(spb_polygon).to_crs(epsg=32636) 
polygon = gpd.GeoDataFrame([{'name': 'Ленинградская область', 'geometry': city[0]}], crs="EPSG:32636")
local_crs = 32636

In [3]:
g = Graph.from_polygon_iduedu(polygon, local_crs= local_crs)

2025-02-10 23:05:43.108 | INFO     | iduedu.modules.drive_walk_builder:get_drive_graph_by_poly:91 - Downloading drive graph from OSM, it may take a while for large territory ...
2025-02-10 23:07:22.727 | INFO     | transport_frames.graphbuilder.graph:_prepare_attrs:146 - Preparing the graph...
2025-02-10 23:08:47.874 | INFO     | transport_frames.graphbuilder.graph:_prepare_attrs:184 - Graph is ready!


In [4]:
n,e = momepy.nx_to_gdf(g.graph)
e.head()

length_meter                                           geometry  \
0      7334.898  LINESTRING (310175.930 6481944.735, 310440.678...   
1      1782.091  LINESTRING (312761.025 6488801.859, 312817.505...   
2      3966.158  LINESTRING (312761.025 6488801.859, 313378.259...   
3       158.791  LINESTRING (316822.012 6514139.318, 316864.213...   
4       209.104  LINESTRING (316822.012 6514139.318, 316878.621...   

        highway   ref  reg   maxspeed  time_min type  node_start  node_end  
0         trunk  Р-23    1  25.000000     4.890  car           0         1  
1         trunk  Р-23    1  25.000000     1.188  car           1       657  
2  unclassified   NaN    3  16.666667     3.966  car           1       841  
3      tertiary   NaN    3  16.666667     0.159  car           2         3  
4      tertiary   NaN    3  16.666667     0.209  car           2         4

## Frame

In [5]:
# polygon regions cities
regions = gpd.read_file('/Users/polina/Desktop/github/transport_frames/data/lo_gdfs/regions_of_russia.geojson')
regions = regions[regions['ISO3166-2']!='RU-CHU']
regions = regions[regions['geometry'].apply(lambda x: isinstance(x, (Polygon, MultiPolygon)))].to_crs(local_crs)

admin_centers = gpd.read_file('/Users/polina/Desktop/github/transport_frames/data/Ленинградская_область 2/Ленинградская_область_district_admin_centres_18_nodes.geojson')
admin_centers['name'] = admin_centers['name18']
admin_centers = admin_centers[['name','geometry']].reset_index().to_crs(local_crs)


In [6]:
from transport_frames.framebuilder.frame import get_frame 
f = get_frame(g,regions,g.polygon,admin_centers)

In [7]:
nf, ef = momepy.nx_to_gdf(f)
nf[nf['city_name'].notna()]

x             y  reg_1  reg_2  nodeID      city_name  \
20     317424.537288  6.514831e+06  False   True      20           Луга   
1117   300046.057665  6.594856e+06  False   True    1117       Волосово   
2106   281081.648956  6.647720e+06  False   True    2106   Сосновый бор   
2560   218931.639885  6.563532e+06  False   True    2560         Сланцы   
4640   368794.578928  6.656527e+06  False   True    4640     Всеволожск   
5291   386977.924317  6.639256e+06  False   True    5291        Кировск   
5508   530500.046837  6.611906e+06  False   True    5508         Тихвин   
5818   344127.577642  6.771835e+06   True  False    5818      Приозерск   
8390   379995.599317  6.602166e+06   True   True    8390          Тосно   
10061  444166.006872  6.590637e+06  False   True   10061         Кириши   
10707  463809.998028  6.639543e+06  False   True   10707         Волхов   
11291  529630.566946  6.733311e+06  False   True   11291  Лодейное Поле   
11777  249848.372324  6.590068e+06  False   True   11777      Кингисепп   
12677  547476.193082  6.593293e+06  False   True   12677   Бокситогорск   
13703  563682.932426  6.754572e+06  False   True   13703     Подпорожье   
18088  268264.670128  6.738082e+06  False   True   18088         Выборг   
21827  337439.207876  6.606941e+06  False   True   21827        Гатчина   

                             geometry  
20     POINT (317424.537 6514830.713)  
1117   POINT (300046.058 6594856.390)  
2106   POINT (281081.649 6647719.646)  
2560   POINT (218931.640 6563532.039)  
4640   POINT (368794.579 6656527.045)  
5291   POINT (386977.924 6639256.308)  
5508   POINT (530500.047 6611905.778)  
5818   POINT (344127.578 6771834.744)  
8390   POINT (379995.599 6602166.176)  
10061  POINT (444166.007 6590636.585)  
10707  POINT (463809.998 6639542.761)  
11291  POINT (529630.567 6733311.492)  
11777  POINT (249848.372 6590067.985)  
12677  POINT (547476.193 6593292.735)  
13703  POINT (563682.932 6754572.330)  
18088  POINT (268264.670 6738081.856)  
21827  POINT (337439.208 6606941.159)

In [8]:
ef[ef['reg']==1].explore()